### Data manipulation example

We read in a SPLICE dataset and format it ready for inclusion in our NN model.

Steps:  

1. Read in the data
2. Create additional variables
3. Apply cutoff
4. Make sure there is one record for every development period
5. Create variables and define which ones you want to use in the model
6. Create train and test datasets

In [3]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns

import torch
import torch.nn as nn
from torch.nn import functional as F

In [4]:
pd.options.display.float_format = '{:,.2f}'.format

### 1. Read in the data from SPLICE  
Here we just use the paid data. Case estimate data is also available in the incurred_1.csv file but we do not use it here

In [5]:
transactions = pd.read_csv(
    f"https://raw.githubusercontent.com/agi-lab/SPLICE/main/datasets/complexity_1/payment_1.csv"
)
transactions

Unnamed: 0  claim_no  pmt_no  occurrence_period  occurrence_time  \
0               1         1       1                  1             0.73   
1               2         1       2                  1             0.73   
2               3         1       3                  1             0.73   
3               4         1       4                  1             0.73   
4               5         1       5                  1             0.73   
...           ...       ...     ...                ...              ...   
19317       19318      3663       2                 40            39.87   
19318       19319      3663       3                 40            39.87   
19319       19320      3663       4                 40            39.87   
19320       19321      3663       5                 40            39.87   
19321       19322      3663       6                 40            39.87   

       claim_size  notidel  setldel  payment_time  payment_period  \
0      232,310.09     0.66    23.21          5.33               6   
1      232,310.09     0.66    23.21         10.09              11   
2      232,310.09     0.66    23.21         18.02              19   
3      232,310.09     0.66    23.21         22.82              23   
4      232,310.09     0.66    23.21         24.61              25   
...           ...      ...      ...           ...             ...   
19317   40,653.72     2.29    10.67         46.40              47   
19318   40,653.72     2.29    10.67         48.45              49   
19319   40,653.72     2.29    10.67         50.24              51   
19320   40,653.72     2.29    10.67         51.76              52   
19321   40,653.72     2.29    10.67         52.84              53   

       payment_size  payment_inflated  payment_delay  
0         13,226.34         13,226.34           3.93  
1         15,685.86         15,685.86           4.76  
2         14,643.28         14,643.28           7.93  
3        170,041.89        170,041.89           4.79  
4         18,712.71         18,712.71           1.79  
...             ...               ...            ...  
19317      2,213.88          2,213.88           1.84  
19318      2,292.75          2,292.75           2.06  
19319      2,367.32          2,367.32           1.78  
19320     28,576.07         28,576.07           1.52  
19321      2,585.46          2,585.46           1.08  

[19322 rows x 13 columns]

### 2. Create additional variables

In [6]:
transactions["noti_period"] = np.ceil(transactions["occurrence_time"] + transactions["notidel"]).astype('int')
transactions["settle_period"] = np.ceil(transactions["occurrence_time"] + transactions["notidel"] + transactions["setldel"]).astype('int')

### 3. Apply cutoff

In [8]:
# Apply a maximum development period
maxdev=40

transactions["development_period"] = np.minimum(transactions["payment_period"] - transactions["occurrence_period"], maxdev)  

transactions

Unnamed: 0  claim_no  pmt_no  occurrence_period  occurrence_time  \
0               1         1       1                  1             0.73   
1               2         1       2                  1             0.73   
2               3         1       3                  1             0.73   
3               4         1       4                  1             0.73   
4               5         1       5                  1             0.73   
...           ...       ...     ...                ...              ...   
19317       19318      3663       2                 40            39.87   
19318       19319      3663       3                 40            39.87   
19319       19320      3663       4                 40            39.87   
19320       19321      3663       5                 40            39.87   
19321       19322      3663       6                 40            39.87   

       claim_size  notidel  setldel  payment_time  payment_period  \
0      232,310.09     0.66    23.21          5.33               6   
1      232,310.09     0.66    23.21         10.09              11   
2      232,310.09     0.66    23.21         18.02              19   
3      232,310.09     0.66    23.21         22.82              23   
4      232,310.09     0.66    23.21         24.61              25   
...           ...      ...      ...           ...             ...   
19317   40,653.72     2.29    10.67         46.40              47   
19318   40,653.72     2.29    10.67         48.45              49   
19319   40,653.72     2.29    10.67         50.24              51   
19320   40,653.72     2.29    10.67         51.76              52   
19321   40,653.72     2.29    10.67         52.84              53   

       payment_size  payment_inflated  payment_delay  noti_period  \
0         13,226.34         13,226.34           3.93            2   
1         15,685.86         15,685.86           4.76            2   
2         14,643.28         14,643.28           7.93            2   
3        170,041.89        170,041.89           4.79            2   
4         18,712.71         18,712.71           1.79            2   
...             ...               ...            ...          ...   
19317      2,213.88          2,213.88           1.84           43   
19318      2,292.75          2,292.75           2.06           43   
19319      2,367.32          2,367.32           1.78           43   
19320     28,576.07         28,576.07           1.52           43   
19321      2,585.46          2,585.46           1.08           43   

       settle_period  development_period  
0                 25                   5  
1                 25                  10  
2                 25                  18  
3                 25                  22  
4                 25                  24  
...              ...                 ...  
19317             53                   7  
19318             53                   9  
19319             53                  11  
19320             53                  12  
19321             53                  13  

[19322 rows x 16 columns]

### 4. Make sure there is one record for every development period (even if nothing happened in that period)
* Create transactions_group for where if more than one payment was made in a development period, that will be grouped into a single record. Create pmt_no count
* Create a range_payment_delay with just 40 development periods in it
* Merge transactions and renge_payment_delay datasets to create clim_head_expeand_dev
    and create payment_period variable and is_settled flag  
* Merge transactions_group and claim_head_expand_dev to bring in payment size and pmt_no from transactions_group

In [9]:
# Transactions summarised by claim/dev:
transactions_group = (transactions
        .groupby(["claim_no", "development_period"], as_index=False)
        .agg({"payment_size": "sum", "pmt_no": "max"})
        .sort_values(by=["claim_no", "development_period"])
)
transactions_group

claim_no  development_period  payment_size  pmt_no
0             1                   5     13,226.34       1
1             1                  10     15,685.86       2
2             1                  18     14,643.28       3
3             1                  22    170,041.89       4
4             1                  24     18,712.71       5
...         ...                 ...           ...     ...
18140      3663                   7      2,213.88       2
18141      3663                   9      2,292.75       3
18142      3663                  11      2,367.32       4
18143      3663                  12     28,576.07       5
18144      3663                  13      2,585.46       6

[18145 rows x 4 columns]

In [11]:
range_payment_delay = pd.DataFrame.from_dict({"development_period": range(0, maxdev)})
range_payment_delay

development_period
0                    0
1                    1
2                    2
3                    3
4                    4
5                    5
6                    6
7                    7
8                    8
9                    9
10                  10
11                  11
12                  12
13                  13
14                  14
15                  15
16                  16
17                  17
18                  18
19                  19
20                  20
21                  21
22                  22
23                  23
24                  24
25                  25
26                  26
27                  27
28                  28
29                  29
30                  30
31                  31
32                  32
33                  33
34                  34
35                  35
36                  36
37                  37
38                  38
39                  39

In [12]:
# Claims header + development periods
claim_head_expand_dev = (
    transactions
    .loc[:, ["claim_no", "claim_size", "occurrence_period", "occurrence_time", "noti_period", "notidel", "setldel", "settle_period"]]
    .drop_duplicates()
).merge(
    range_payment_delay,
    how="cross"
).assign(
    payment_period=lambda df: (df.occurrence_period + df.development_period),
    is_settled=lambda df: (df.occurrence_period + df.development_period) >= df.settle_period
)
claim_head_expand_dev

claim_no  claim_size  occurrence_period  occurrence_time  noti_period  \
0              1  232,310.09                  1             0.73            2   
1              1  232,310.09                  1             0.73            2   
2              1  232,310.09                  1             0.73            2   
3              1  232,310.09                  1             0.73            2   
4              1  232,310.09                  1             0.73            2   
...          ...         ...                ...              ...          ...   
146515      3663   40,653.72                 40            39.87           43   
146516      3663   40,653.72                 40            39.87           43   
146517      3663   40,653.72                 40            39.87           43   
146518      3663   40,653.72                 40            39.87           43   
146519      3663   40,653.72                 40            39.87           43   

        notidel  setldel  settle_period  development_period  payment_period  \
0          0.66    23.21             25                   0               1   
1          0.66    23.21             25                   1               2   
2          0.66    23.21             25                   2               3   
3          0.66    23.21             25                   3               4   
4          0.66    23.21             25                   4               5   
...         ...      ...            ...                 ...             ...   
146515     2.29    10.67             53                  35              75   
146516     2.29    10.67             53                  36              76   
146517     2.29    10.67             53                  37              77   
146518     2.29    10.67             53                  38              78   
146519     2.29    10.67             53                  39              79   

        is_settled  
0            False  
1            False  
2            False  
3            False  
4            False  
...            ...  
146515        True  
146516        True  
146517        True  
146518        True  
146519        True  

[146520 rows x 11 columns]

In [13]:
# create the dataset
dat = claim_head_expand_dev.merge(
    transactions_group,
    how="left",
    on=["claim_no", "development_period"],
).fillna(0)
dat

claim_no  claim_size  occurrence_period  occurrence_time  noti_period  \
0              1  232,310.09                  1             0.73            2   
1              1  232,310.09                  1             0.73            2   
2              1  232,310.09                  1             0.73            2   
3              1  232,310.09                  1             0.73            2   
4              1  232,310.09                  1             0.73            2   
...          ...         ...                ...              ...          ...   
146515      3663   40,653.72                 40            39.87           43   
146516      3663   40,653.72                 40            39.87           43   
146517      3663   40,653.72                 40            39.87           43   
146518      3663   40,653.72                 40            39.87           43   
146519      3663   40,653.72                 40            39.87           43   

        notidel  setldel  settle_period  development_period  payment_period  \
0          0.66    23.21             25                   0               1   
1          0.66    23.21             25                   1               2   
2          0.66    23.21             25                   2               3   
3          0.66    23.21             25                   3               4   
4          0.66    23.21             25                   4               5   
...         ...      ...            ...                 ...             ...   
146515     2.29    10.67             53                  35              75   
146516     2.29    10.67             53                  36              76   
146517     2.29    10.67             53                  37              77   
146518     2.29    10.67             53                  38              78   
146519     2.29    10.67             53                  39              79   

        is_settled  payment_size  pmt_no  
0            False          0.00    0.00  
1            False          0.00    0.00  
2            False          0.00    0.00  
3            False          0.00    0.00  
4            False          0.00    0.00  
...            ...           ...     ...  
146515        True          0.00    0.00  
146516        True          0.00    0.00  
146517        True          0.00    0.00  
146518        True          0.00    0.00  
146519        True          0.00    0.00  

[146520 rows x 13 columns]

Only include records for a claim that is after the notification period

In [14]:
dat = dat.loc[dat.payment_period >= dat.noti_period].copy()
dat

claim_no  claim_size  occurrence_period  occurrence_time  noti_period  \
1              1  232,310.09                  1             0.73            2   
2              1  232,310.09                  1             0.73            2   
3              1  232,310.09                  1             0.73            2   
4              1  232,310.09                  1             0.73            2   
5              1  232,310.09                  1             0.73            2   
...          ...         ...                ...              ...          ...   
146515      3663   40,653.72                 40            39.87           43   
146516      3663   40,653.72                 40            39.87           43   
146517      3663   40,653.72                 40            39.87           43   
146518      3663   40,653.72                 40            39.87           43   
146519      3663   40,653.72                 40            39.87           43   

        notidel  setldel  settle_period  development_period  payment_period  \
1          0.66    23.21             25                   1               2   
2          0.66    23.21             25                   2               3   
3          0.66    23.21             25                   3               4   
4          0.66    23.21             25                   4               5   
5          0.66    23.21             25                   5               6   
...         ...      ...            ...                 ...             ...   
146515     2.29    10.67             53                  35              75   
146516     2.29    10.67             53                  36              76   
146517     2.29    10.67             53                  37              77   
146518     2.29    10.67             53                  38              78   
146519     2.29    10.67             53                  39              79   

        is_settled  payment_size  pmt_no  
1            False          0.00    0.00  
2            False          0.00    0.00  
3            False          0.00    0.00  
4            False          0.00    0.00  
5            False     13,226.34    1.00  
...            ...           ...     ...  
146515        True          0.00    0.00  
146516        True          0.00    0.00  
146517        True          0.00    0.00  
146518        True          0.00    0.00  
146519        True          0.00    0.00  

[142841 rows x 13 columns]

### 5. Create variables and define which ones you want to use in the model

In [15]:
# Clean close to zero values
dat["payment_size"] = np.where(abs(dat.payment_size) < 1e-2, 0.0, dat.payment_size)

# Cumulative payments
dat["payment_size_cumulative"] = dat[["claim_no", "payment_size"]].groupby('claim_no').cumsum()
dat["log1_paid_cumulative"] = np.log1p(dat.payment_size_cumulative)

dat["payment_to_prior_period"] = dat["payment_size_cumulative"] - dat["payment_size"]
dat["has_payment_to_prior_period"] = np.where(dat.payment_to_prior_period > 1e-2, 1, 0)

dat["paid_dev_factor"] = dat["payment_size_cumulative"]/dat["payment_to_prior_period"]*dat["has_payment_to_prior_period"]

dat["pmt_no"] = dat.groupby("claim_no")["pmt_no"].cummax()

dat["max_paid_dev_factor"] = dat.groupby('claim_no')['paid_dev_factor'].cummax().fillna(0)
dat["min_paid_dev_factor"] = dat.groupby('claim_no')['paid_dev_factor'].cummin().fillna(0)

Show records just for an individual claim - here claim_no 1

In [17]:
dat[dat['claim_no'] == 1]

claim_no  claim_size  occurrence_period  occurrence_time  noti_period  \
1          1  232,310.09                  1             0.73            2   
2          1  232,310.09                  1             0.73            2   
3          1  232,310.09                  1             0.73            2   
4          1  232,310.09                  1             0.73            2   
5          1  232,310.09                  1             0.73            2   
6          1  232,310.09                  1             0.73            2   
7          1  232,310.09                  1             0.73            2   
8          1  232,310.09                  1             0.73            2   
9          1  232,310.09                  1             0.73            2   
10         1  232,310.09                  1             0.73            2   
11         1  232,310.09                  1             0.73            2   
12         1  232,310.09                  1             0.73            2   
13         1  232,310.09                  1             0.73            2   
14         1  232,310.09                  1             0.73            2   
15         1  232,310.09                  1             0.73            2   
16         1  232,310.09                  1             0.73            2   
17         1  232,310.09                  1             0.73            2   
18         1  232,310.09                  1             0.73            2   
19         1  232,310.09                  1             0.73            2   
20         1  232,310.09                  1             0.73            2   
21         1  232,310.09                  1             0.73            2   
22         1  232,310.09                  1             0.73            2   
23         1  232,310.09                  1             0.73            2   
24         1  232,310.09                  1             0.73            2   
25         1  232,310.09                  1             0.73            2   
26         1  232,310.09                  1             0.73            2   
27         1  232,310.09                  1             0.73            2   
28         1  232,310.09                  1             0.73            2   
29         1  232,310.09                  1             0.73            2   
30         1  232,310.09                  1             0.73            2   
31         1  232,310.09                  1             0.73            2   
32         1  232,310.09                  1             0.73            2   
33         1  232,310.09                  1             0.73            2   
34         1  232,310.09                  1             0.73            2   
35         1  232,310.09                  1             0.73            2   
36         1  232,310.09                  1             0.73            2   
37         1  232,310.09                  1             0.73            2   
38         1  232,310.09                  1             0.73            2   
39         1  232,310.09                  1             0.73            2   

    notidel  setldel  settle_period  development_period  payment_period  \
1      0.66    23.21             25                   1               2   
2      0.66    23.21             25                   2               3   
3      0.66    23.21             25                   3               4   
4      0.66    23.21             25                   4               5   
5      0.66    23.21             25                   5               6   
6      0.66    23.21             25                   6               7   
7      0.66    23.21             25                   7               8   
8      0.66    23.21             25                   8               9   
9      0.66    23.21             25                   9              10   
10     0.66    23.21             25                  10              11   
11     0.66    23.21             25                  11              12   
12     0.66    23.21   

Define which variables you want to use in the model

output_field and youtput are also created to define the y variate for use in the model

In [19]:
# Potential features for model later:
data_cols = [
    "claim_no",
    "occurrence_time", 
    "notidel", 
    "development_period", 
    "pmt_no",
    "log1_paid_cumulative",
    "max_paid_dev_factor",
    "min_paid_dev_factor",
]

list_of_features = data_cols
output_field = ["claim_size"]
youtput="claim_size"

dat.loc[:, data_cols + [youtput]]
#dat.loc[:, list_of_features + output_field]

claim_no  occurrence_time  notidel  development_period  pmt_no  \
1              1             0.73     0.66                   1    0.00   
2              1             0.73     0.66                   2    0.00   
3              1             0.73     0.66                   3    0.00   
4              1             0.73     0.66                   4    0.00   
5              1             0.73     0.66                   5    1.00   
...          ...              ...      ...                 ...     ...   
146515      3663            39.87     2.29                  35    6.00   
146516      3663            39.87     2.29                  36    6.00   
146517      3663            39.87     2.29                  37    6.00   
146518      3663            39.87     2.29                  38    6.00   
146519      3663            39.87     2.29                  39    6.00   

        log1_paid_cumulative  max_paid_dev_factor  min_paid_dev_factor  \
1                       0.00                 0.00                 0.00   
2                       0.00                 0.00                 0.00   
3                       0.00                 0.00                 0.00   
4                       0.00                 0.00                 0.00   
5                       9.49                 0.00                 0.00   
...                      ...                  ...                  ...   
146515                 10.61                 4.01                 1.00   
146516                 10.61                 4.01                 1.00   
146517                 10.61                 4.01                 1.00   
146518                 10.61                 4.01                 1.00   
146519                 10.61                 4.01                 1.00   

        claim_size  
1       232,310.09  
2       232,310.09  
3       232,310.09  
4       232,310.09  
5       232,310.09  
...            ...  
146515   40,653.72  
146516   40,653.72  
146517   40,653.72  
146518   40,653.72  
146519   40,653.72  

[142841 rows x 9 columns]

## 6. Create train and test datasets.  
We provide three types of indicators here for reference, but in our NN example we only use train_ind  

* train_ind creates a split by claim - 'rectangular data'
* train_ind_time is what you would use if you wanted to split the datasets by calendar period
* cv_ind is what you might use if you were doing cross validation

In [20]:
cutoff=maxdev

dat["train_ind"] = (dat.claim_no % 10 >= 4)
dat["train_ind_time"] = (dat.payment_period <= cutoff)
dat["cv_ind"] = dat.payment_period % 5
dat

claim_no  claim_size  occurrence_period  occurrence_time  noti_period  \
1              1  232,310.09                  1             0.73            2   
2              1  232,310.09                  1             0.73            2   
3              1  232,310.09                  1             0.73            2   
4              1  232,310.09                  1             0.73            2   
5              1  232,310.09                  1             0.73            2   
...          ...         ...                ...              ...          ...   
146515      3663   40,653.72                 40            39.87           43   
146516      3663   40,653.72                 40            39.87           43   
146517      3663   40,653.72                 40            39.87           43   
146518      3663   40,653.72                 40            39.87           43   
146519      3663   40,653.72                 40            39.87           43   

        notidel  setldel  settle_period  development_period  payment_period  \
1          0.66    23.21             25                   1               2   
2          0.66    23.21             25                   2               3   
3          0.66    23.21             25                   3               4   
4          0.66    23.21             25                   4               5   
5          0.66    23.21             25                   5               6   
...         ...      ...            ...                 ...             ...   
146515     2.29    10.67             53                  35              75   
146516     2.29    10.67             53                  36              76   
146517     2.29    10.67             53                  37              77   
146518     2.29    10.67             53                  38              78   
146519     2.29    10.67             53                  39              79   

        ...  payment_size_cumulative  log1_paid_cumulative  \
1       ...                     0.00                  0.00   
2       ...                     0.00                  0.00   
3       ...                     0.00                  0.00   
4       ...                     0.00                  0.00   
5       ...                13,226.34                  9.49   
...     ...                      ...                   ...   
146515  ...                40,653.72                 10.61   
146516  ...                40,653.72                 10.61   
146517  ...                40,653.72                 10.61   
146518  ...                40,653.72                 10.61   
146519  ...                40,653.72                 10.61   

        payment_to_prior_period  has_payment_to_prior_period  paid_dev_factor  \
1                          0.00                            0              NaN   
2                          0.00                            0              NaN   
3                          0.00                            0              NaN   
4                          0.00                            0              NaN   
5                          0.00                            0              NaN   
...                         ...                          ...              ...   
146515                40,653.72                            1             1.00   
146516                40,653.72                            1             1.00   
146517                40,653.72                            1             1.00   
146518                40,653.72                            1             1.00   
146519                40,653.72                            1             1.00   

        max_paid_dev_factor  min_paid_dev_factor  train_ind  train_ind_time  \
1                      0.00                 0.00      False            True   
2                      0.00                 0.00      False            True   
3                      0.00                 0.00      False            True   
4                      0.00                 0.00    

In [21]:
X_train = (dat.loc[(dat.train_ind == 1), list_of_features])
y_train = (dat.loc[(dat.train_ind == 1), youtput])

X_test = (dat.loc[(dat.train_ind == 0), list_of_features])
y_test = (dat.loc[(dat.train_ind == 0), youtput])

X = (dat.loc[:, list_of_features])
y = (dat.loc[:, youtput])

Save file to disk. ***Remember to change the directory reference below to where you want it to be saved***. 

In [22]:
dirname_in="/DataDirectoryPath/"
filename_in="data.csv"

dat.to_csv(
    dirname + filename
)